In [1]:
%load_ext autoreload
%autoreload 2

import matplotlib.pyplot as plt
import networkx as nx
import numpy as np
import os
import pickle
import time
from tqdm.notebook import tqdm

import torch
torch.set_default_tensor_type(torch.DoubleTensor)

from spatial_scene_grammars.constraints import *
from spatial_scene_grammars.nodes import *
from spatial_scene_grammars.rules import *
from spatial_scene_grammars.scene_grammar import *
from spatial_scene_grammars.visualization import *
from spatial_scene_grammars_examples.table.grammar import *
from spatial_scene_grammars.parsing import *
from spatial_scene_grammars.sampling import *
from spatial_scene_grammars.parameter_estimation import *
from spatial_scene_grammars.dataset import *

import meshcat
import meshcat.geometry as meshcat_geom

In [2]:
if 'vis' not in globals():
    vis = meshcat.Visualizer()
vis.delete()
base_url = "http://127.0.0.1"
meshcat_url = base_url + ":" + vis.url().split(":")[-1]
print("Meshcat url: ", meshcat_url)
'''
from IPython.display import HTML
HTML("""
    <div style="height: 400px; width: 100%; overflow-x: auto; overflow-y: hidden; resize: both">
    <iframe src="{url}" style="width: 100%; height: 100%; border: none"></iframe>
</div>
""".format(url=meshcat_url))
'''

You can open the visualizer by visiting the following URL:
http://127.0.0.1:7002/static/
Meshcat url:  http://127.0.0.1:7002/static/


'\nfrom IPython.display import HTML\nHTML("""\n    <div style="height: 400px; width: 100%; overflow-x: auto; overflow-y: hidden; resize: both">\n    <iframe src="{url}" style="width: 100%; height: 100%; border: none"></iframe>\n</div>\n""".format(url=meshcat_url))\n'

In [3]:
# Set up grammar
grammar = SpatialSceneGrammar(
    root_node_type = Table,
    root_node_tf = drake_tf_to_torch_tf(RigidTransform(p=[0.0, 0., 0.8]))
)

# Single unconstrained draw
torch.random.manual_seed(40)
tree = grammar.sample_tree(detach=True)
draw_scene_tree_contents_meshcat(tree, zmq_url=vis.window.zmq_url,  prefix="sample/contents")
draw_scene_tree_structure_meshcat(tree, zmq_url=vis.window.zmq_url,  prefix="sample/structure", node_sphere_size=0.01,
                                  linewidth=5)

[2022-01-14 20:29:09.582] [console] [warning] FindResource ignoring DRAKE_RESOURCE_ROOT='/home/gizatt/drake' because it does not contain a 'drake' subdirectory.


In [7]:
# Fix scene
projected_tree = project_tree_to_feasibility(tree, zmq_url=vis.window.zmq_url)
draw_scene_tree_contents_meshcat(projected_tree, zmq_url=vis.window.zmq_url, prefix="projected_sample")

[2022-01-14 20:15:43.551] [console] [warning] FindResource ignoring DRAKE_RESOURCE_ROOT='/home/gizatt/drake' because it does not contain a 'drake' subdirectory.


Logfile: 

         S N O P T  7.4-1.2  (Feb 2015)
1
 
 SNMEMA EXIT 100 -- finished successfully
 SNMEMA INFO 104 -- memory requirements estimated
1
 
 Parameters

 Files
 -----
 Solution file..........         0       Old basis file ........         0       Standard input.........         5
 Insert file............         0       New basis file ........         0       (Printer)..............        10
 Punch file.............         0       Backup basis file......         0       (Specs file)...........         0
 Load file..............         0       Dump file..............         0       Standard output........         6

 Frequencies
 -----------
 Print frequency........       100       Check frequency........        60       Save new basis map.....       100
 Summary frequency......       100       Factorization frequency        50       Expand frequency.......     10000

 QP subproblems
 --------------
 QPsolver Cholesky......
 Scale tolerance........     0.900       Minor 

In [9]:
simulated_tree = project_tree_to_feasibility_via_sim(projected_tree, zmq_url=vis.window.zmq_url)

KeyboardInterrupt: 

In [94]:
# Simulate scene
simulate_scene_tree(tree, T=10, timestep=0.001, target_realtime_rate=0.1, meshcat=vis.window.zmq_url)

Connecting to meshcat-server at zmq_url=tcp://127.0.0.1:6007...
You can open the visualizer by visiting the following URL:
http://127.0.0.1:7007/static/
Connected to meshcat-server.


KeyboardInterrupt: 

In [6]:
# Constraints
class ObjectsOnTableConstraint(Constraint):
    def __init__(self):
        lb = torch.tensor([-Table.WIDTH/2.+0.1, -Table.WIDTH/2.-0.1, 0.001])
        ub = torch.tensor([Table.WIDTH/2.+0.1, Table.WIDTH/2.-0.1, 100.])
        super().__init__(
            lower_bound=lb,
            upper_bound=ub
        )
    def eval(self, scene_tree):
        tables = scene_tree.find_nodes_by_type(Table)
        xyzs = [] # in parent table frame
        for table in tables:
            # Collect table children xyz poses in table frame
            objs = [node for node in scene_tree.get_children_recursive(table) if isinstance(node, TabletopObjectTypes)]
            for obj in objs:
                offset = torch.matmul(table.rotation.T, obj.translation - table.translation)
                xyzs.append(offset)
        if len(xyzs) > 0:
            return torch.stack(xyzs, axis=0)
        else:
            return torch.empty(size=(0, 3))
    def add_to_ik_prog(self, scene_tree, ik, mbp, mbp_context, node_to_free_body_ids_map):
        raise NotImplementedError()

class ObjectSpacingConstraint(Constraint):
    # Objects all a minimum distance apart on tabletop
    def __init__(self):
        lb = torch.tensor([0.])
        ub = torch.tensor([np.inf])
        super().__init__(
            lower_bound=lb,
            upper_bound=ub
        )
    def eval(self, scene_tree):
        tables = scene_tree.find_nodes_by_type(Table)
        all_dists = []
        for table in tables:
            objs = [node for node in scene_tree.get_children_recursive(table) if isinstance(node, TabletopObjectTypes)
                    and not isinstance(scene_tree.get_parent(node), SteamerBottom)]
            if len(objs) <= 1:
                continue
            xys = torch.stack([obj.translation[:2] for obj in objs], axis=0)
            keepout_dists = torch.tensor([obj.KEEPOUT_RADIUS for obj in objs])
            N = xys.shape[0]
            xys_rowwise = xys.unsqueeze(1).expand(-1, N, -1)
            keepout_dists_rowwise = keepout_dists.unsqueeze(1).expand(-1, N)
            xys_colwise = xys.unsqueeze(0).expand(N, -1, -1)
            keepout_dists_colwise = keepout_dists.unsqueeze(0).expand(N, -1)
            dists = (xys_rowwise - xys_colwise).square().sum(axis=-1)
            keepout_dists = (keepout_dists_rowwise + keepout_dists_colwise)

            # Get only lower triangular non-diagonal elems
            rows, cols = torch.tril_indices(N, N, -1)
            # Make sure pairwise dists > keepout dists
            dists = (dists - keepout_dists.square())[rows, cols].reshape(-1, 1)

            all_dists.append(dists)
        if len(all_dists) > 0:
            return torch.cat(all_dists, axis=0)
        else:
            return torch.empty(size=(0, 1))
    def add_to_ik_prog(self, scene_tree, ik, mbp, mbp_context, node_to_free_body_ids_map):
        raise NotImplementedError()

constraints = [
    ObjectsOnTableConstraint(),
    ObjectSpacingConstraint()
]
hmc_tree = deepcopy(tree)
samples = do_fixed_structure_hmc_with_constraint_penalties(
    grammar, hmc_tree, num_samples=50, subsample_step=10,
    with_nonpenetration=False, zmq_url=vis.window.zmq_url,
    constraints=constraints,
    kernel_type="NUTS", max_tree_depth=7, target_accept_prob=0.65
    #kernel_type="HMC", num_steps=1, step_size=1E-2 # Langevin-ish
)

tensor([[ 4.0806e-02],
        [ 4.7833e-01],
        [ 2.0431e-01],
        [ 2.6906e-01],
        [ 1.1640e-01],
        [ 6.7620e-03],
        [ 4.0784e-01],
        [ 4.9423e-01],
        [ 4.4581e-01],
        [ 2.4165e-01],
        [ 3.2658e-01],
        [ 2.6133e-01],
        [ 1.4127e-01],
        [ 4.1664e-02],
        [ 4.2380e-02],
        [ 1.4114e-01],
        [-1.2194e-04],
        [ 1.0782e-01],
        [ 8.1921e-02],
        [ 5.5802e-01],
        [ 2.6255e-01],
        [ 2.9711e-02],
        [ 1.8418e-04],
        [ 1.5035e-01],
        [ 4.1240e-02],
        [ 2.5993e-01],
        [ 1.0775e-01],
        [ 2.7422e-02],
        [ 2.1434e-01],
        [ 1.1560e-01],
        [ 2.9762e-02],
        [-2.7257e-02],
        [ 1.2849e-01],
        [-9.2751e-03],
        [ 1.0201e-01],
        [ 1.4115e-02],
        [-1.9954e-02],
        [ 5.2881e-02],
        [ 3.0524e-01],
        [ 1.2085e-01],
        [ 1.7280e-01],
        [ 1.2005e-01],
        [ 1.2630e-01],
        [-1

Warmup:   0%|          | 0/75 [00:00, ?it/s]

tensor([[ 1.3019e-02],
        [ 1.0293e+00],
        [ 6.4150e-01],
        [ 6.1798e-01],
        [ 3.3051e-01],
        [ 1.3025e-02],
        [ 3.4349e-01],
        [ 1.5982e-01],
        [ 4.9019e-01],
        [ 3.0560e-01],
        [ 2.1942e-01],
        [ 6.0439e-02],
        [ 3.8241e-01],
        [ 1.8035e-01],
        [ 1.2523e-03],
        [ 2.7053e-01],
        [ 1.8549e-01],
        [ 3.9757e-01],
        [ 1.9318e-01],
        [ 5.5570e-01],
        [ 2.9608e-01],
        [ 2.1661e-01],
        [ 6.5403e-02],
        [ 2.2221e-01],
        [ 5.5236e-02],
        [ 1.6906e-01],
        [ 4.3525e-02],
        [ 6.6280e-02],
        [ 5.2175e-01],
        [ 2.4405e-01],
        [ 6.4125e-02],
        [ 8.8010e-03],
        [ 8.8461e-02],
        [ 5.4258e-02],
        [ 2.9412e-01],
        [ 4.0027e-02],
        [ 4.7497e-01],
        [ 2.2134e-01],
        [ 3.6229e-02],
        [-2.5947e-02],
        [ 1.7685e-01],
        [ 8.4016e-02],
        [ 1.6984e-01],
        [ 7

tensor([[1.9119e+01],
        [4.6660e+02],
        [3.1285e+02],
        [8.3676e+02],
        [6.2651e+02],
        [5.3872e+01],
        [6.7189e+02],
        [4.6871e+02],
        [4.4511e+01],
        [5.0610e+01],
        [1.0957e+03],
        [8.2736e+02],
        [3.3724e+02],
        [3.1262e+02],
        [1.4217e+02],
        [4.6209e+02],
        [3.0075e+02],
        [7.7957e+00],
        [6.9243e+01],
        [2.3625e+01],
        [2.5384e+02],
        [4.1951e+02],
        [2.8397e+02],
        [6.8697e+00],
        [7.6373e+01],
        [8.6449e+01],
        [4.4018e+02],
        [2.6920e+01],
        [5.5727e+02],
        [3.7218e+02],
        [3.9317e+01],
        [8.3218e+01],
        [6.7273e+00],
        [1.5011e+02],
        [1.3541e+01],
        [7.7774e+01],
        [4.1732e+02],
        [2.7955e+02],
        [4.3730e+00],
        [7.4505e+01],
        [7.7082e+01],
        [4.1659e+02],
        [2.1007e+01],
        [3.2941e-01],
        [6.7686e+01],
        [5

tensor([[ 0.0438],
        [ 1.1317],
        [ 0.6270],
        [ 0.7695],
        [ 0.3636],
        [-0.0040],
        [ 0.4764],
        [ 0.3046],
        [ 0.3001],
        [ 0.2098],
        [ 0.3759],
        [ 0.1393],
        [ 0.1765],
        [ 0.0642],
        [ 0.0456],
        [ 0.4925],
        [ 0.2186],
        [ 0.5294],
        [ 0.3416],
        [ 0.7741],
        [ 0.3521],
        [ 0.3989],
        [ 0.1328],
        [ 0.1228],
        [ 0.0239],
        [ 0.0915],
        [-0.0206],
        [ 0.2575],
        [ 0.1014],
        [-0.0036],
        [ 0.6091],
        [ 0.3567],
        [ 0.4595],
        [ 0.1946],
        [ 0.0689],
        [ 0.1529],
        [ 0.1308],
        [ 0.0118],
        [ 0.6074],
        [ 0.3586],
        [ 0.5001],
        [ 0.2130],
        [ 0.0466],
        [ 0.1642],
        [-0.0561],
        [ 0.5968],
        [ 0.2391],
        [ 0.1854],
        [ 0.0939],
        [ 0.4993],
        [ 0.1721],
        [ 0.0292],
        [ 0.

...

tensor([[ 7.5807e-02],
        [ 1.1994e+00],
        [ 5.7194e-01],
        [ 6.9234e-01],
        [ 2.4246e-01],
        [ 3.4294e-02],
        [ 6.7062e-01],
        [ 2.7745e-01],
        [ 2.0840e-01],
        [ 7.8187e-02],
        [ 6.8029e-01],
        [ 2.3823e-01],
        [ 5.7189e-02],
        [-1.3733e-02],
        [ 3.0542e-02],
        [ 5.9964e-02],
        [ 4.4000e-02],
        [ 7.8691e-01],
        [ 4.2776e-01],
        [ 6.0131e-01],
        [ 4.5497e-01],
        [ 6.0938e-02],
        [ 1.3183e-01],
        [ 1.1262e+00],
        [ 6.2731e-01],
        [ 4.0306e-01],
        [ 5.6848e-01],
        [ 2.8794e-01],
        [ 2.9097e-01],
        [ 2.9932e-02],
        [ 2.3225e-01],
        [ 3.5646e-02],
        [ 5.4545e-02],
        [ 2.7568e-02],
        [ 1.7877e-01],
        [ 2.5440e-01],
        [ 1.0098e+00],
        [ 4.7035e-01],
        [-1.4396e-04],
        [ 7.1154e-02],
        [ 3.8415e-01],
        [ 1.2507e-01],
        [ 5.5454e-01],
        [ 1

tensor([[ 0.0234],
        [ 1.0501],
        [ 0.6042],
        [ 0.6423],
        [ 0.3041],
        [ 0.0169],
        [ 0.5235],
        [ 0.3838],
        [ 0.5060],
        [ 0.4322],
        [ 0.3680],
        [ 0.1872],
        [ 0.2912],
        [ 0.1846],
        [ 0.0228],
        [ 0.4247],
        [ 0.1657],
        [ 0.1592],
        [ 0.0248],
        [ 0.5372],
        [ 0.2346],
        [ 0.1349],
        [ 0.0031],
        [ 0.3400],
        [ 0.1240],
        [ 0.3350],
        [ 0.1187],
        [ 0.0386],
        [ 0.1772],
        [ 0.1316],
        [ 0.6094],
        [ 0.4063],
        [ 0.0122],
        [ 0.0262],
        [ 0.3927],
        [ 0.1486],
        [ 0.4572],
        [ 0.3150],
        [ 0.7564],
        [ 0.4447],
        [ 1.3187],
        [ 0.8247],
        [ 0.2063],
        [ 0.2563],
        [ 0.9086],
        [ 0.2709],
        [ 0.0897],
        [ 0.2044],
        [ 0.0812],
        [ 0.1000],
        [-0.0131],
        [ 0.0915],
        [ 0.

Sample: 100%|██████████| 75/75 [01:48,  1.45s/it, step size=3.13e-01, acc. prob=0.089]

tensor([[ 3.7773e-02],
        [ 1.0589e+00],
        [ 5.6481e-01],
        [ 7.2361e-01],
        [ 3.2860e-01],
        [-7.8645e-03],
        [ 7.8771e-01],
        [ 4.2693e-01],
        [ 1.4294e-01],
        [ 1.2121e-01],
        [ 7.5093e-01],
        [ 3.5434e-01],
        [ 1.2073e-02],
        [ 1.5346e-04],
        [ 2.7567e-02],
        [ 4.1131e-01],
        [ 2.1142e-01],
        [ 4.1163e-01],
        [ 2.7380e-01],
        [ 7.2585e-01],
        [ 4.1371e-01],
        [ 5.4800e-02],
        [-2.5363e-02],
        [ 4.8086e-01],
        [ 2.6648e-01],
        [ 3.3533e-01],
        [ 2.8178e-01],
        [ 2.1197e-01],
        [ 2.5897e-01],
        [ 8.2855e-02],
        [ 3.1449e-01],
        [ 1.6658e-01],
        [ 6.1690e-02],
        [ 1.1640e-01],
        [ 4.2303e-01],
        [ 3.4099e-02],
        [ 5.6597e-01],
        [ 2.5335e-01],
        [ 1.1862e-01],
        [ 6.6301e-02],
        [ 4.2470e-01],
        [ 1.6874e-01],
        [ 2.4385e-02],
        [ 2

tensor([[ 5.0104e-02],
        [ 1.1816e+00],
        [ 6.2171e-01],
        [ 7.2392e-01],
        [ 3.0658e-01],
        [ 1.8123e-02],
        [ 5.4913e-01],
        [ 2.6132e-01],
        [ 3.2800e-01],
        [ 2.2747e-01],
        [ 5.7535e-01],
        [ 2.2310e-01],
        [ 1.3174e-01],
        [ 5.3884e-02],
        [ 1.8469e-02],
        [ 3.2449e-01],
        [ 2.0006e-01],
        [ 6.5116e-01],
        [ 3.5724e-01],
        [ 7.9146e-01],
        [ 5.2225e-01],
        [ 2.8499e-01],
        [ 4.9335e-02],
        [ 2.3124e-01],
        [ 5.6026e-02],
        [ 1.5091e-01],
        [ 5.0024e-02],
        [ 1.8508e-01],
        [ 2.4541e-01],
        [ 4.4513e-02],
        [ 3.2899e-01],
        [ 1.4128e-01],
        [ 9.6186e-03],
        [ 1.9210e-02],
        [ 3.8323e-01],
        [-1.3849e-03],
        [ 1.1089e-01],
        [ 1.3748e-01],
        [ 9.7058e-01],
        [ 5.7070e-01],
        [ 8.3903e-01],
        [ 6.5118e-01],
        [ 2.3803e-02],
        [ 2

In [7]:
k=4
draw_scene_tree_contents_meshcat(samples[-k], zmq_url=vis.window.zmq_url,  prefix="hmc_samples/%d/contents" % k)
draw_scene_tree_structure_meshcat(samples[-k], zmq_url=vis.window.zmq_url,  prefix="hmc_samples/%d/structure" % k)

In [10]:
# Do final projeciton pass
final_tree = project_tree_to_feasibility(samples[-k], do_forward_sim=True, timestep=0.001, T=1.)
draw_scene_tree_contents_meshcat(samples[-k], zmq_url=vis.window.zmq_url,  prefix="final_sample/contents")
draw_scene_tree_structure_meshcat(samples[-k], zmq_url=vis.window.zmq_url,  prefix="final_sample/structure")

Logfile: 

         S N O P T  7.4-1.2  (Feb 2015)
1
 
 SNMEMA EXIT 100 -- finished successfully
 SNMEMA INFO 104 -- memory requirements estimated
1
 
 Parameters

 Files
 -----
 Solution file..........         0       Old basis file ........         0       Standard input.........         5
 Insert file............         0       New basis file ........         0       (Printer)..............        10
 Punch file.............         0       Backup basis file......         0       (Specs file)...........         0
 Load file..............         0       Dump file..............         0       Standard output........         6

 Frequencies
 -----------
 Print frequency........       100       Check frequency........        60       Save new basis map.....       100
 Summary frequency......       100       Factorization frequency        50       Expand frequency.......     10000

 QP subproblems
 --------------
 QPsolver Cholesky......
 Scale tolerance........     0.900       Minor 

In [11]:
# Save that scene out for use in another notebook
with open("example_feasible_sampled_scene.pickle", "wb") as f:
    pickle.dump(final_tree, f)